In [1]:
import tweepy
import os

auth = tweepy.OAuthHandler("xfnR2T3pIfWHCi6AiG0qgqa66",
                           "Nqcf6CV0v38MEslrrQdylT9qOVJV2Ml8tvQfRdAn68QaSOV9tF") #Set up the app keys
auth.set_access_token("1384725604155678721-Gpr9D569SBGjL29iSDAcSQcAPWzrpU",
                      "nE2Yb9Bqa6Cw447KNX78PbHbfUfOcVGTdTzPv8u2S94L8") #set up your user tokens

api = tweepy.API(auth, wait_on_rate_limit=True)

In [119]:
import json
from csv import writer

dat=list()
with open ('tweets4.json', 'r') as f:
    for l in f.readlines():
        if not l.strip (): # skip empty lines
            continue

        json_data = json.loads (l)
        dat.append(json_data)

ids = [tweet['id_str'] for tweet in dat]
times = [tweet['created_at'] for tweet in dat]
users = [tweet['user']['name'] for tweet in dat]
texts = [tweet['text'] for tweet in dat]
lats = [(T['geo']['coordinates'][0] if T['geo'] else None) for T in dat]
lons = [(T['geo']['coordinates'][1] if T['geo'] else None) for T in dat]
place_names = [(T['place']['full_name'] if T['place'] else None) for T in dat]
place_types = [(T['place']['place_type'] if T['place'] else None) for T in dat]
locations = [(T['user']['location'] if T['user'] else None) for T in dat]
retweets_count = [tweet['retweet_count'] for tweet in dat]
#retweets_status_count = [(T['quoted_status']['retweet_count'] if T['quoted_status'] else None) for T in dat]
favourites_count = [(T['user']['favourites_count'] if T['user'] else None) for T in dat]


In [120]:
import pandas as pd
import numpy as np

d = {'id': ids, 'created': times, 'place name': place_names, 'place type': place_types,
    'location': locations, 'favourites_count': favourites_count}
df = pd.DataFrame(data=d)
df.to_csv (r'tweets_file.csv', index = None)

In [121]:
df = df.fillna(value='None')
df

id                         created    place name  \
0      1443040038745411596  Wed Sep 29 02:28:50 +0000 2021          None   
1      1443040060367048705  Wed Sep 29 02:28:55 +0000 2021          None   
2      1443040061201608709  Wed Sep 29 02:28:55 +0000 2021  Avondale, AZ   
3      1443040064905224195  Wed Sep 29 02:28:56 +0000 2021          None   
4      1443040071628857362  Wed Sep 29 02:28:58 +0000 2021          None   
...                    ...                             ...           ...   
11534  1443160901390065668  Wed Sep 29 10:29:06 +0000 2021          None   
11535  1443160916661526533  Wed Sep 29 10:29:09 +0000 2021          None   
11536  1443160935728828416  Wed Sep 29 10:29:14 +0000 2021          None   
11537  1443160944159469569  Wed Sep 29 10:29:16 +0000 2021          None   
11538  1443160951658795016  Wed Sep 29 10:29:18 +0000 2021          None   

      place type                                        location  \
0           None                                    Brooklyn, NY   
1           None                                      Frisco, TX   
2           city                                     Phoenix, AZ   
3           None                                            None   
4           None                                            None   
...          ...                                             ...   
11534       None  London, UK,Terra, Sol system, Milky Way Galaxy   
11535       None                                Wien, Österreich   
11536       None                                            None   
11537       None                                            None   
11538       None                                            None   

       favourites_count  
0                  1862  
1                   766  
2                  5243  
3                  4913  
4                    42  
...                 ...  
11534             90533  
11535             17324  
11536              5732  
11537              8050  
11538              2328  

[11539 rows x 6 columns]

In [118]:
dat[0]['user']['favourites_count']

1862

In [122]:
import preprocessor as p
from textblob import TextBlob

tweet_texts = [p.api.clean(tweet['text']) for tweet in dat]
tweet_texts

[': SHARE THIS(ft. )',
 ": $AMC: Feeling bored? Feeling despondent? That's how this works. This slow bleed of discomfort to make you want to sell an",
 'Nothing to see here much like and is doing something odd . Something s',
 'was gonna film a little weekly overview for the days ahead but then I noticed something interesting...Editing it',
 ': $AMC',
 '[Last Hours]Stocks Trending among Elite Traders: . $CEI . $TSLA . $AMZN . $AAPL5. $LCID6',
 ': An $GME, $AMC story in parts.',
 ': Citadel delaying PFOF settlements for over a month -a chat between and (see the full video at: h',
 'Options traders:',
 ': At what point does the $AMC community start holding people like accountable? He swooped into the mo',
 '',
 ": Here's 's chart.But thiws isn't price being charted.This is volume being charted.We know price = volumeWe kno",
 '[Last Hours]Stocks Trending among Elite Traders: . $CEI . $UPST . $GME . $LCID5. $AMZN6.',
 ': The fact that citadel responded to us (retail) is very bullish. Billi

In [123]:
sentiment_dict= {'positive': 0, 'neutral': 0, 'negative': 0}
body_sent = []

blobs = [TextBlob(text) for text in tweet_texts]
for blob in blobs:
    if blob.sentiment.polarity > 0:
        sentiment = '+'
        sentiment_dict['positive'] += 1 
    elif blob.sentiment.polarity == 0:
        sentiment = 'n'
        sentiment_dict['neutral'] += 1 
    else:
        sentiment = '-'
        sentiment_dict['negative'] += 1 
    
    body_sent.append(sentiment)
    print(f'{sentiment} : {blob}\n')
        
print('Positive:', sentiment_dict['positive'])
print(' Neutral:', sentiment_dict['neutral'])
print('Negative:', sentiment_dict['negative'])

df['body_sent'] = body_sent

n : : SHARE THIS(ft. )

- : : $AMC: Feeling bored? Feeling despondent? That's how this works. This slow bleed of discomfort to make you want to sell an

+ : Nothing to see here much like and is doing something odd . Something s

- : was gonna film a little weekly overview for the days ahead but then I noticed something interesting...Editing it

n : : $AMC

n : [Last Hours]Stocks Trending among Elite Traders: . $CEI . $TSLA . $AMZN . $AAPL5. $LCID6

n : : An $GME, $AMC story in parts.

+ : : Citadel delaying PFOF settlements for over a month -a chat between and (see the full video at: h

n : Options traders:

n : : At what point does the $AMC community start holding people like accountable? He swooped into the mo

n : 

n : : Here's 's chart.But thiws isn't price being charted.This is volume being charted.We know price = volumeWe kno

n : [Last Hours]Stocks Trending among Elite Traders: . $CEI . $UPST . $GME . $LCID5. $AMZN6.

+ : : The fact that citadel responded to us (retail) is very


+ : : Thanks for the confirmation. $AMC

n : Aditya Birla Sun Life AMC Ltd IPO Details:

n : : If I learned thing about the Doge community, its the fact that we GET THINGS DONE! )COINBASE ADDS DOGE )ROBIN

n : I needed this thread. Im wondering what t

n : Sir hdfc amc bought share at rs , what to do sir ? Badi pareshani mein hu sir...

- : : Sold all my crypto for more $AMC. I might just be retarded, but I'm not afraid to find out. Do or die, bitches. See you

+ : : el apertura investigacin penal contra Kenia Carrillo titular del Tribunal de Juicio AMC: p

n : : Fiscal Generam informa sobre investigacin penal contra Kenia Carrillo, jueza del tribunal de juicio AMC. Por el caso

+ : new matrix movie commemorative NFT lets get it started, bring in that additional revenue, lets make

n : : Imagine life as Citadel , a multi-billion dollar company using Twitter to explain themselves to a perso

n : RALLreallyRALLwhoHasTheirHandUpTheBack0fThisPUPPTAMC

n : $902K

n : : Say it louder for th


n : : babann telefonu var myd diye konuya dalan salak amc bir hafta aralksz dvsem yine rahatlayamam dayanamyorum b

n : $AMC $GME

n : The theory is they were trying to cellarbox GME/AMC. Cellar boxing is where they s

n : Do they have something against potatoes

n : : I think we struck a nerve with

n : Aditya Birla AMC IPO: IPO will open today, know investment strategy and what is going on in gray marketrate

n : THIS IS THE WAY!! Thank you ! This wouldnt be possible with you!

n : : Ken Griffin's Cars with VIN 's. $AMC $GME

+ : : BREAKING NEWS HEADLINECitadel posting to Twitter after months to target the very people they claim to represent,

- : I mean I don't know what to tell you, coins go up, they go down, the market has been

+ : Chicken fried rice was delicious, but the fortune cookies was a lot more.$AMC $MOASS

+ : : As for the low volume... I'm in love with it.How fast do drive when you're turning your car around?

n : 

n : members. $GME

n : : Ken Griffin's Cars with VIN


n : $AMC $GME

n : : $AMC Have HF covered ? No.

n : : Apes, do you feel should demand the do a share count for $AMC?

+ : : WOAHH HELLO AA WHAT A PLEASANT SURPRISE TO HEAR FROM YOU TONIGHT! DID YOU HEAR THAT KEN GRIFFIN LIED

n : Bullish!

n : selling my rblx acc for amazon giftcard (CA) i also hve some pets in adopt me and k amc

n : : Facts. $GME $AMC

- : : I previously tweeted AMCs new -second Nicole Kidman television commercial. She also made different -second commercials

- : : I previously tweeted AMCs new -second Nicole Kidman television commercial. She also made different -second commercials

- : Looking forward to enjoying these women only IMAX and prime screens at AMC even though Im still mad that they adde

- : : I previously tweeted AMCs new -second Nicole Kidman television commercial. She also made different -second commercials

+ : : Aditya Birla Sun Life AMC is LIVE Now! ABSL AMC is a joint venture between ABCL &amp; Sun Life AMC. It

- : "ad:" AMC THE WALKING DEAD TR


- : : So now turning off the buy button is a conspiracy theory? Let me guess, so are Dark Pools &amp; PFOF. $AMC

+ : AMCs literally have one job - manage money - to keep growing. But is that one factor enough to make an AMC a good i

+ : : And here is the third of our new -second Nicole Kidman television commercials. These ads are one of many things

- : : Remember: Ken is not scared of Congress or Sec. He is scared of public sentiment making Citadel look

n : : FOCKERS I figured it out, hashtag unlocks Citadel final level BOSS $AMC

+ : : And here is the third of our new -second Nicole Kidman television commercials. These ads are one of many things

n : Umm, what?? All I gotta say is

n : : FYI Family and while I am at it also NFA $AMC

n : On the offensive ... LETS GO!

+ : The AMAZING ADAM is on fire, playing offense!!! Whoop whoop!!

- : : I previously tweeted AMCs new -second Nicole Kidman television commercial. She also made different -second commercials

+ : : A lot of Apes wo

...

n : : I wasted so much time.Spent a ton of ETH on art and it was just sitting in my wallet.I couldnt figure out what to do n

+ : : Ape Nation $AMC Put yourself in his shoes. -Maybe the better approach would be to ask a friend to beat the stock

+ : : OMGSo Much DiscountI Am Gonna Vuy Through ThisAMC Should Accept S

- : : The shorts will attempts to cover at least -20 million shares tomorrow by pm to keep the exchange reported S

n : : Amcm nasl beendiniz mi

+ : $SOFI working it's way into the top most mentioned on wallstreetbets over the last daysVia

+ : : It is darn amazing what shares of Twitter will get you these days. $GME$AMC ht

+ : : The difference between $AMC Ape crowd and is pretty obvious: The XRP-Ripple case has some real meat, conflict

- : Doesn't matter price is fake, shares are synthetic.$GME

n : 

- : : The shorts will attempts to cover at least -20 million shares tomorrow by pm to keep the exchange reported S

n : *IPO Opens Today* *Aditya Birla Sun Life AMC IPO 


+ : I can't believe that Kim did this on the latest episode of Better Call Saul! Nacho will be shocked at this new reve

- : : I will tweet everyday until $AMC squeezes

n : Citadel orchestrated the entire GameStop saga court document reveals via /r/wallstreetbets

- : Listen carefully .... instead of playing on the words demonstrated in front of a c

+ : : Funny how all this information has come out but no one seems to know how many shares of $AMC and $GME were sold

n : Derler bana akamcMermer kafam az sancmGelemem, gelememGelemem yolunuza yok inanc

+ : : And here is the third of our new -second Nicole Kidman television commercials. These ads are one of many things

- : You made a mess by raging on AMC shares and issuing billions of fake shares.

+ : *Starting with $15k, down to $10k, back up to $85k, Lot of thanks to this chat $ATOS

- : You made a mess by raging on AMC shares and issuing billions of fake shares.

+ : Happy birthday Nikul BhaisahabAMC COUNCILLOR KUBER NAGAR WARDAH


- : : Daily advice from The Professor:If you run a multi billion dollar firm and deal with trillions of dollars each day, its pro

n : $amc $gme

n : Corruption on a daily basis. Ongoing. Obvious. Unpunished. Still, maybe today youll post a ni

+ : : PLEASE TELL ME HOW HEDGEFUNDS MALICIOUSLY SHORTING COMPANIES INTO BANKRUPTCY IS GOOD FOR THE US ECONOMY!! THIS

n : You forgot LSE:MXC lots of positives for this company including AMC holdings orde

+ : : Dont forget more nodes are needed!Especially with Robinhood wallets coming &amp; AMC accepting Help

n : $AMC

- : : I will tweet everyday until $AMC squeezes

+ : As I see people post pics of amc price of how they purchased more shares, it baffles me that they do it with a Robinhood account.

n : : $AMC $GME

n : : Pregunta : Quien ganar la pelea entre el Fiscal Tarek y la Juez Kenia Carrillo ? Creo que Tarek se est curando en salud

+ : Nothing new to see here. Obviously you guys are not involved in GME at all and so when they finally



n : : FOCKERS I figured it out, hashtag unlocks Citadel final level BOSS $AMC

n : Telefonda Bosalmak steyen, Azgn Bayanlar, Kzl Bozulmadan, Amcn Yalatmak isteyen Kzlar, G

n : : In case you missed it (1/2)Heres the interview with Charles Payne and Trey aka Tray from today.$AMC

n : :

n : : In case you missed it (2/2)Cc: Cc: Cc: $AMC

n : of the $AMC messages are "hedgies are the devil!!!!"

- : : We will not leave. Ive been poor my whole life. Time to turn the tables

+ : : Day of giveaway. Today we have a hot one: x just launched by experienced DeFi team and upcoming DAO.

n : Hey, Kenny, just so you know.. no cell, no sell. $GME

n : Telefonda Bosalmak steyen, Azgn Bayanlar, Kzl Bozulmadan, Amcn Yalatmak isteyen Kzlar, G

+ : : Best idea for AMC customers. is one of the best entertainment platform.

- : : I previously tweeted AMCs new -second Nicole Kidman television commercial. She also made different -second commercials

n : 

n : :

- : $AMC green stay fucking green

n : : $AMC


n : $NAKD $GEVO $GME

n : : When should I giveaway the AMC?

+ : : If you invested the second stimulus check $600 into $AMC it would now be worth $9,868.42I hear the hedge funds are in a tig

n : $AMC $GME

+ : What are your thoughts about the FAREWELL MESSAGE Citadel left to $AMC ? taking action on them for th

n : Bruh$AMC $GME

- : : I previously tweeted AMCs new -second Nicole Kidman television commercial. She also made different -second commercials

+ : : Panic-mode.ON! Good sum-up from a reddit ape about Citadels tweets

+ : : And here is the third of our new -second Nicole Kidman television commercials. These ads are one of many things

n : Grasim is the parent of AMC biz, so Grasim valuation may rise.

+ : : new matrix movie commemorative NFT lets get it started, bring in that additional revenue, lets make $A

+ : I played this interesting Quiz on Amazon I played this interesting Quiz on Amazon-Play games at Amazon FunZone

n : 

+ : : And here is the third of our new -second 

In [124]:
df.to_csv('outputsent.csv', index=False)

In [131]:
df = pd.read_csv ('reddit.csv')
df["body"].fillna(df["title"], inplace=True)
df

title  score      id  \
0      It's not about the money, it's about sending a...     55  l6ulcx   
1      Math Professor Scott Steiner says the numbers ...    110  l6uibd   
2                                        Exit the system      0  l6uhhn   
3      NEW SEC FILING FOR GME! CAN SOMEONE LESS RETAR...     29  l6ugk6   
4      Not to distract from GME, just thought our AMC...     71  l6ufgy   
...                                                  ...    ...     ...   
52106  Everything I've learned about being on Wall St...   1011  od9xfn   
52107  I Accidentally YOLOed Half My Portfolio After ...    510  od97ek   
52108                      $53k TO $306K in just 2 days.   1190  od7008   
52109       Average Annual Return on Investments for WSB     74  od77kx   
52110  Genuine question about hypothetical stock shor...     19  od75w3   

                                                     url  comms_num  \
0                        https://v.redd.it/6j75regs72e61          6   
1                        https://v.redd.it/ah50lyny62e61         23   
2      https://www.reddit.com/r/wallstreetbets/commen...         47   
3      https://sec.report/Document/0001193125-21-019848/         74   
4                    https://i.redd.it/4h2sukb662e61.jpg        156   
...                                                  ...        ...   
52106                    https://v.redd.it/dfkjjyjae3971         87   
52107  https://www.reddit.com/r/wallstreetbets/commen...        288   
52108                https://i.redd.it/k0pkc2m4i2971.png        237   
52109  https://www.reddit.com/r/wallstreetbets/commen...        194   
52110  https://www.reddit.com/r/wallstreetbets/commen...         64   

            created                                               body  \
0      1.611863e+09  It's not about the money, it's about sending a...   
1      1.611862e+09  Math Professor Scott Steiner says the numbers ...   
2      1.611862e+09  The CEO of NASDAQ pushed to halt trading “to g...   
3      1.611862e+09  NEW SEC FILING FOR GME! CAN SOMEONE LESS RETAR...   
4      1.611862e+09  Not to distract from GME, just thought our AMC...   
...             ...                                                ...   
52106  1.625359e+09  Everything I've learned about being on Wall St...   
52107  1.625357e+09  tl;dr at bottom\n\nSo after using DD from [u/C...   
52108  1.625349e+09                      $53k TO $306K in just 2 days.   
52109  1.625349e+09  I was having a discussion with my friends abou...   
52110  1.625349e+09  So I want to start this off by saying you prob...   

                 timestamp  
0      2021-01-28 21:37:41  
1      2021-01-28 21:32:10  
2      2021-01-28 21:30:35  
3      2021-01-28 21:28:57  
4      2021-01-28 21:26:56  
...                    ...  
52106  2021-07-04 03:43:04  
52107  2021-07-04 02:55:38  
52108  2021-07-04 00:42:06  
52109  2021-07-04 00:54:20  
52110  2021-07-04 00:51:34  

[52111 rows x 8 columns]

In [132]:
bodys = [body for body in df.body]

In [133]:
bodys

["It's not about the money, it's about sending a message. 🚀💎🙌",
 'Math Professor Scott Steiner says the numbers spell DISASTER for Gamestop shorts',
 'The CEO of NASDAQ pushed to halt trading “to give investors a chance to recalibrate their positions”.\n\n[https://mobile.twitter.com/Mediaite/status/1354504710695362563](https://mobile.twitter.com/Mediaite/status/1354504710695362563)\n\nNow SEC is investigating, brokers are disallowing buying more calls. This is the institutions flat out admitting they will change the rules to bail out the rich but if it happens to us, we get a “well shucks you should have known investing is risky! have you tried cutting out avocados and coffee, maybe doing Uber on the side?”\n\nWe may have collectively driven up enough sentiment in wall street to make other big players go long on GME with us (we do not have the money to move the stock as much as it did alone). we didn’t hurt wall street as a whole, just a few funds went down while others went up and pro

In [134]:
bodys = [p.clean(body) for body in bodys]

In [135]:
bodys

["It's not about the money, it's about sending a message.",
 'Math Professor Scott Steiner says the numbers spell DISASTER for Gamestop shorts',
 'The CEO of NASDAQ pushed to halt trading to give investors a chance to recalibrate their positions.[]()Now SEC is investigating, brokers are disallowing buying more calls. This is the institutions flat out admitting they will change the rules to bail out the rich but if it happens to us, we get a well shucks you should have known investing is risky! have you tried cutting out avocados and coffee, maybe doing Uber on the side?We may have collectively driven up enough sentiment in wall street to make other big players go long on GME with us (we do not have the money to move the stock as much as it did alone). we didnt hurt wall street as a whole, just a few funds went down while others went up and profited off the shorts the same as us. The media wants to pin the blame on us.It should be crystal clear that this is a rigged game by now. Its tim

In [136]:
sentiment_dict= {'positive': 0, 'neutral': 0, 'negative': 0}
title_sent = []

blobs = [TextBlob(title) for title in titles]
for blob in blobs:
    if blob.sentiment.polarity > 0:
        sentiment = '+'
        sentiment_dict['positive'] += 1 
    elif blob.sentiment.polarity == 0:
        sentiment = 'n'
        sentiment_dict['neutral'] += 1 
    else:
        sentiment = '-'
        sentiment_dict['negative'] += 1 
    
    print(f'{sentiment} : {blob}\n')
    title_sent.append(sentiment)
        
print('Positive:', sentiment_dict['positive'])
print(' Neutral:', sentiment_dict['neutral'])
print('Negative:', sentiment_dict['negative'])

df['title_sent'] = title_sent

n : It's not about the money, it's about sending a message.

n : Math Professor Scott Steiner says the numbers spell DISASTER for Gamestop shorts

n : Exit the system

- : NEW SEC FILING FOR GME! CAN SOMEONE LESS RETARDED THAN ME PLEASE INTERPRET?

+ : Not to distract from GME, just thought our AMC brothers should be aware of this

n : WE BREAKING THROUGH

n : SHORT STOCK DOESN'T HAVE AN EXPIRATION DATE

n : THIS IS THE MOMENT

- : Currently Holding AMC and NOK - Is it retarded that I think I should move it all to GME today?

n : I have nothing to say but BRUH I am speechless TO THE MOON

n : We need to keep this movement going, we all can make history!

n : GME Premarket Musk approved

n : Once you're done with GME - $AG and $SLV, the gentleman's short squeeze, driven by macro fundamentals

n : $GME price has nothing to do with fundamentals and everything to do with financial economics

- : I Love You Retards!!!!

n : wasnt a meme. GME

n : To The Mass Relays & Beyond

n : I come back


n : CGX will go to $200!!!!!!............To the moom!!!!!!!!!!!!!!!!

+ : Freetrade has AMC, NOK, BB with GME & BBBY on the plus service use this link for a free share!

n : ROLLS ROYCE GUYS LETS GET IT TO THE MOOON!!!!

n : Robinhood containment thread

n : Drive ZOM while theyre still focused on GME and AMC!!!

n : How can I now invest into $GME

n : NOK is legit. NOK is a setup by WS Bots. Which is it? Short Interest is %?

n : robinhood blocking gme and others?

n : Trading wont let me Buy $GME

n : Is this reality?

n : Is it JNUG stock a BUY BUY BUY

+ : IMO $PRTY can be GME2.0 or GME3.0. We tried squeezing them in Dec. They didnt listen. Short ratio consistently going up...HOLD $GME BUY $PRTY. thought?

n : Our stocks taken off? HOLD THE LINE!!!! DONT SELLLL KEEP WHAT YOU HAVE!!! REBUILD RE-RES!!! (NAKD) IS NEXT IF RH DOESNT OPEN OUR STOCKS!!!!

n : Review bomb brokers that restrict buying?

n : When you couldnt join the chain

n : Robinhood class action/squeeze PLTR

n : How l


n : unity gone. But anyways buy GME

- : RETARDS- NOKIA (NOK) is actually a leading company in G. HOLD OR BUY NOKIA (NOK)

n : What is the point of equilibrium to bankrupt the GME Hedge Funds?

n : Which platforms are still trading GME?

n : Celltrion is under attack by short sellers in south korea

n : AAL flies to the Moon. Lets Go.

+ : Robinhood is the free app on the iOS app store

n : GOT EM

n : Pushing the line!

+ : For those interested in SLV:

n : Robinhood canceled my orders. What are we dumping money into thats STILL on Robinhood?

n : Oh, you need to cover your short? Thats terrible. Best I can do is $1,000 + Not selling these until then.

n : Apologies if this was already made and posted (I am not a financial advisor, nor is this financial advice)

n : 

+ : Are mods on your side for sure?

n : $NOK NEEDS PUSH

n : Portnoy posted this

n : AMC buy the dip

n : Discord

n : TD AMERITRADE ADDED TO THE LIST OF MANIPULATORS!

- : With Robinhood down, Square Cash is still le


n : This is Where We Fight, This is Where They DIE - Tony Mandarich

+ : We didn't come this far, to only come this far.

n : GME TO THE MOON! (In my opinion of course)

+ : All Good!

n : Wheres everyone at witj SLV??

- : Well Im fucked boys

n : DOGE COIN now halted on Robinhood

- : Robinhood stopped trading this tight when I sold some other shares to buy in. Any way for me to buy this now through another trading platform... like now? I'm ready to join the bandwagon and squeeze the big guys.

- : Not like I used you anyways you filthy peasant

n : A THEORY (Cc- Dave Portnoy)

+ : HIGH REALITY ISNT REAL

- : UPDATE... guys they were blocking GME earlier but if you came late to the revolution there is still a way to make money with Dogecoin. Lets get em. WE NEED GAINS TOO

n : Thank to the guys and gals around the globe for continuing to buy and hold.

+ : THE HEDGE FUNDS ARE MELTING - STAY STRONG AUTISTS

- : Your r/bitcoin friends salute you. If a traditional Wall Street firm had 

n : Where does a noob start?

n : NOK

- : Total market manipulation when a stock drops % and PUT options go negative!!!

n : Kodak. Another opportunity to punish the short sellers?

n : Forward

n : BB buy time baby

n : BUY THE DIP GME BACK TO AND BEYOND

n : Whats happening to Nokia???!!!

n : Robinhood limits Dogecoin

n : Robinhood cancelled my NOK NOK

+ : First time cussing to my dad | GME to the MOON

n : Are we going to let this people intimidate us???????

n : GET IN THIS DISCORD BOYS

n : Push it for me boys!!

n : I LIKE THE STONK $GME

n : Replacement for RobinHood? We Must Stick Together and not give in!

n : BUY THE NOK DIP!!!

n : Pennys

+ : Most Shorted Stocks Update: Here Come The Microcaps

n : Big boys are counter attacking.

n : $SPCE TO THE MOOM

+ : REPOST THIS AS MANY TIMES AS YOU CAN

n : Come on!

n : If i can't buy AMC I'm buying Doge

n : Why you should buy $AMC AND USING CASH APP.

n : ORGANIGRAM ((OGI)) SUNDIAL GROWERS ((SNDL)) DOGECOIN CRYPTO LETS GOOO



...


n : Amazon Said to Make $9 Billion Offer for MGM

n : I'm somewhat of a day trader myself HMU for financial advice

n : TSLA

+ : We are posting UWMC positions today right? Been buying down since $9

+ : Why tomorrow may be the the day to buy $CNK... a potentially epic play to go along with the $AMC piss missile

- : CLOV.....Long on shares....Options seems worthless

+ : Did you ever hear the Tragedy of Darth Jartek the wise?

+ : $GME TA - BIG BREAKOUT TODAY - SETUP LOOKS BETTER THAN IT EVER HAS

- : Electric Vehicle Startup Canoos CEO Discloses SEC Investigation

n : Renewable Energy Set to Skyrocket Under Biden Administration

+ : I love goooooooooooooold -Johann van der Smut (and silver too)

- : Sold my poor person house for $80k. Need $300k to attract higher quality whores

n : k yolo on uwmc

n : Think about why GME & AMC are shorted simultaneously.. Suppose Netflix had the chance to take over Videogames and In-person movies revenue... Lucrative

n : UWMC: The Thesis on Why I'


n : Roblox Accused in Suit of Ripping Off Kids With Bogus Purchases - Bloomberg

- : AMC YOLO average

n : Tesla Phases Out Radar Sensors, Shifts to Camera-Based Autopilot

n : been in this since day one! AMC will make me richer than that troll elon

n : Margin Royale

n : AMC Shares at $17.08 Wish Us Luck

n : Well Well Well how the turn Tables have!

n : Around the campfire with DFV

n : Lord of the Memes: The Two Stonks

- : PROUD AMC RETARD K YOLO INTO c

n : Hows my application? Am I in?

- : Still hanging on to Coinbase options after the past weeks. Crawling up from the wreckage.

- : $62k YOLO into $AMC pray for me. I dont usually do this.

n : ZYME YOLO

n : $PINS and needles

- : yet one more (very short and crude) $GME DD

- : SNDL is building an empire and VLNS is the missing piece

n : $MVIS DD by u/hiddengooru (mods let this man post)

n : NVDA DD

+ : Can't invest in SpaceX but you can invest in Concrete

n : A thesis on the disillusion called Robinhood

- : BB been limp


n : Think you guys will bring me to %?

n : Diamond Hands Rocket - UWMC In My Pocket (with positions)

+ : The Weekly DD - Mountain Pass Materials (MP): The Rare Earth Miner

- : I know it was a rough day for a lot of people but wkhs is still running

- : Forget the rocket to the moon. There are gains to be made on the RIDE down to the Earth's core! % gain in one day on Lordstown Motors puts.

n : Fraternal Association of Gambling Gentlemen and Yacht Degenerates for June ,

+ : $CLF Diamond Handed Today +81k, Did I win the casino? $975 -> k in weeks

n : CLNE

n : +33K SIR_JACK_ALOT IS MY KING K YOLO split evenly between CLF and BARK paid off big today Sold CLF letting BARK ride

n : FIZZ will keep me up all night

n : $700k RKT YOLO. Lets Go!!

+ : I bet no one paid a higher price for a WISH today

n : I'm a scientist, here's why I'm bullish on Inovio (INO)

+ : Am I doing this right?

n : Baby ape born today CLOV gains to RKT

+ : $UWMC This rocket is fueled and ready

+ : $WISH yol


+ : Who the fuck doesnt love dogs?

n : $PAVE, US Infrastructure Development ETF

n : $RGR - Has been printing for me these last months and the FBI gives you the information you need to estimate earnings

+ : $CLF - Huge BRRRR signals forming - strike while the iron is hot!

n : $OCGN short term opportunity

n : The hospitality industry (hotels) is just about to rebound and I'm thinking Ashford Hospitality Trust, Inc. ??????

n : $WISH in honor of u/Unusual-Obligation-7 YOLO

n : GEVO = Moon Landing

n : Cautious expectations on TSLA for next week?

n : Part | Coupang Inc. - Pressure is building... A Counterparty Incentive to Suppress Price

+ : Shares on WISH. Good Luck everyone.

n : Zapping shorts with G - $TEF

n : About $LZB, not a financial advice

n : Infrastructure... $CLF

+ : $BBBY Technical analysis- Break out confirmed

n : Biden Says He Has Infrastructure Deal With Senate Group. HRC futures hit $1800 ATH. My CLF shares are having a steel erection

+ : Finally got some ten

n : PLAY giant bull flag

+ : $VRT is the best shit that nobody is talking about

n : Sr-dtc-2021-005 gets published tomorrow in federal register so enforced from tomorrow

n : Why I bought SOFI and PLTR , $200,000 Combined

+ : Short WSB - First Blood

+ : Duolingo is filing an IPO LOL

n : RIG - Supply and Demand for Oil and Recovery Play. Short DD Included Below

n : Supreme Court Justice Clarence Thomas questions federal marijuana prohibition in IRS case

n : PRPL NRPLS- Fear not, for I am with thee

+ : $118k BARK Position. I Love Bitches!

+ : Taking the safe route with $PSFE

+ : $SOFI, SO GOOD - M YOLO

n : k $SOFI all in. SOFLY!

n : K in AMC, Going to the moon

n : Unlocking the Recipe for Tendies - An Investigation from Walmart to Wallstreet

- : WOOF is primed for a Angry bull run!

n : $SJR Shaw Communications The Mega Acquisition and Earnings Play

+ : SOFI - So Fly

n : Sundial Growers Inc. (SNDL) Outpaces Stock Market Gains: What You Should Know

n : Ford (F) needs a pi

In [137]:
df

title  score      id  \
0      It's not about the money, it's about sending a...     55  l6ulcx   
1      Math Professor Scott Steiner says the numbers ...    110  l6uibd   
2                                        Exit the system      0  l6uhhn   
3      NEW SEC FILING FOR GME! CAN SOMEONE LESS RETAR...     29  l6ugk6   
4      Not to distract from GME, just thought our AMC...     71  l6ufgy   
...                                                  ...    ...     ...   
52106  Everything I've learned about being on Wall St...   1011  od9xfn   
52107  I Accidentally YOLOed Half My Portfolio After ...    510  od97ek   
52108                      $53k TO $306K in just 2 days.   1190  od7008   
52109       Average Annual Return on Investments for WSB     74  od77kx   
52110  Genuine question about hypothetical stock shor...     19  od75w3   

                                                     url  comms_num  \
0                        https://v.redd.it/6j75regs72e61          6   
1                        https://v.redd.it/ah50lyny62e61         23   
2      https://www.reddit.com/r/wallstreetbets/commen...         47   
3      https://sec.report/Document/0001193125-21-019848/         74   
4                    https://i.redd.it/4h2sukb662e61.jpg        156   
...                                                  ...        ...   
52106                    https://v.redd.it/dfkjjyjae3971         87   
52107  https://www.reddit.com/r/wallstreetbets/commen...        288   
52108                https://i.redd.it/k0pkc2m4i2971.png        237   
52109  https://www.reddit.com/r/wallstreetbets/commen...        194   
52110  https://www.reddit.com/r/wallstreetbets/commen...         64   

            created                                               body  \
0      1.611863e+09  It's not about the money, it's about sending a...   
1      1.611862e+09  Math Professor Scott Steiner says the numbers ...   
2      1.611862e+09  The CEO of NASDAQ pushed to halt trading “to g...   
3      1.611862e+09  NEW SEC FILING FOR GME! CAN SOMEONE LESS RETAR...   
4      1.611862e+09  Not to distract from GME, just thought our AMC...   
...             ...                                                ...   
52106  1.625359e+09  Everything I've learned about being on Wall St...   
52107  1.625357e+09  tl;dr at bottom\n\nSo after using DD from [u/C...   
52108  1.625349e+09                      $53k TO $306K in just 2 days.   
52109  1.625349e+09  I was having a discussion with my friends abou...   
52110  1.625349e+09  So I want to start this off by saying you prob...   

                 timestamp title_sent  
0      2021-01-28 21:37:41          n  
1      2021-01-28 21:32:10          n  
2      2021-01-28 21:30:35          n  
3      2021-01-28 21:28:57          -  
4      2021-01-28 21:26:56          +  
...                    ...        ...  
52106  2021-07-04 03:43:04          n  
52107  2021-07-04 02:55:38          -  
52108  2021-07-04 00:42:06          n  
52109  2021-07-04 00:54:20          -  
52110  2021-07-04 00:51:34          +  

[52111 rows x 9 columns]

In [42]:
df.to_csv('redditsent.csv', index=False)

In [166]:
from collections import Counter

split_it = list()
for body in bodys:
    split = body.split()
    for word in split:
        split_it.append(word)

Counter = Counter(split_it)
most_occur = Counter.most_common(50)
print(most_occur)

[('the', 206397), ('to', 144964), ('and', 119881), ('a', 104709), ('of', 100707), ('is', 79141), ('in', 69482), ('I', 59283), ('that', 50942), ('for', 48781), ('on', 43182), ('this', 40643), ('you', 38679), ('are', 36029), ('it', 33764), ('with', 28968), ('be', 28892), ('have', 28638), ('at', 26972), ('they', 25885), ('as', 24842), ('will', 24319), ('not', 23878), ('but', 22030), ('their', 20638), ('from', 18867), ('we', 18223), ('my', 18137), ('all', 17971), ('has', 17509), ('was', 17485), ('or', 16923), ('can', 15979), ('The', 15306), ('by', 15115), ('if', 14588), ('%', 14338), ('just', 14205), ('more', 14066), ('up', 13626), ('like', 13563), ('an', 13495), ('your', 13485), ('stock', 13046), ('about', 12886), ('so', 12498), ('GME', 12183), ('This', 11719), ('shares', 11610), ('what', 11601)]


In [167]:
from collections import Counter

split_it = list()
for body in texts:
    split = body.split()
    for word in split:
        split_it.append(word)

Counter = Counter(split_it)
most_occur = Counter.most_common(50)
print(most_occur)

[('RT', 7270), ('the', 4057), ('to', 2943), ('of', 2597), ('I', 2207), ('is', 2187), ('$AMC', 2123), ('#AMC', 1980), ('and', 1674), ('#KenGriffinLied', 1625), ('a', 1433), ('new', 1314), ('in', 1280), ('@CEOAdam:', 1225), ('Nicole', 1217), ('Kidman', 1211), ('television', 1198), ('30-second', 1198), ('are', 1167), ('AMC', 1155), ('you', 1063), ('for', 930), ('on', 918), ('this', 792), ('3', 737), ('made', 731), ('also', 720), ('tweeted', 694), ('AMC’s', 694), ('different', 687), ('our', 684), ('commercial.', 684), ('She', 683), ('@AMCTheatres', 683), ('previously', 681), ('60-second', 681), ('commercials…', 680), ('one', 677), ('that', 646), ('The', 634), ('$GME', 633), ('@citsecurities', 609), ('many', 607), ('Citadel', 602), ('here', 591), ('And', 576), ('#GME', 553), ('These', 546), ('at', 537), ('will', 526)]
